# Business Data Challenge - Team 1

In [1]:
import pandas as pd
import numpy as np


Configuration de l'accès aux données

In [2]:
import os
import s3fs
# Create filesystem object
S3_ENDPOINT_URL = "https://" + os.environ["AWS_S3_ENDPOINT"]
fs = s3fs.S3FileSystem(client_kwargs={'endpoint_url': S3_ENDPOINT_URL})


## Exemple sur bdc2324-data/11

In [10]:
BUCKET = "bdc2324-data/11"
fs.ls(BUCKET)

['bdc2324-data/11/11campaign_stats.csv',
 'bdc2324-data/11/11campaigns.csv',
 'bdc2324-data/11/11categories.csv',
 'bdc2324-data/11/11countries.csv',
 'bdc2324-data/11/11currencies.csv',
 'bdc2324-data/11/11customer_target_mappings.csv',
 'bdc2324-data/11/11customersplus.csv',
 'bdc2324-data/11/11event_types.csv',
 'bdc2324-data/11/11events.csv',
 'bdc2324-data/11/11facilities.csv',
 'bdc2324-data/11/11link_stats.csv',
 'bdc2324-data/11/11pricing_formulas.csv',
 'bdc2324-data/11/11product_packs.csv',
 'bdc2324-data/11/11products.csv',
 'bdc2324-data/11/11products_groups.csv',
 'bdc2324-data/11/11purchases.csv',
 'bdc2324-data/11/11representation_category_capacities.csv',
 'bdc2324-data/11/11representations.csv',
 'bdc2324-data/11/11seasons.csv',
 'bdc2324-data/11/11structure_tag_mappings.csv',
 'bdc2324-data/11/11suppliers.csv',
 'bdc2324-data/11/11tags.csv',
 'bdc2324-data/11/11target_types.csv',
 'bdc2324-data/11/11targets.csv',
 'bdc2324-data/11/11tickets.csv']

In [23]:
# Chargement de toutes les données
liste_base = ['customer_target_mappings', 'customersplus', 'target_types', 'tags', 'events', 'tickets', 'representations', 'purchases', 'products']

for nom_base in liste_base:
    FILE_PATH_S3 = 'bdc2324-data/11/11' + nom_base + '.csv'
    with fs.open(FILE_PATH_S3, mode="rb") as file_in:
        globals()[nom_base] = pd.read_csv(file_in, sep=",")

In [24]:
# Jointure
var_choosed = ['id_x', 'customer_id','product_id', 'purchase_date', 'type_of', 'is_from_subscription']
merge_1 = pd.merge(purchases, tickets, left_on='id', right_on='purchase_id', how='inner')[var_choosed]

var_choosed.extend(['amount', 'is_full_price', 'representation_id'])
merge_2 = pd.merge(products, merge_1, left_on='id', right_on='product_id', how='inner')[var_choosed]

var_choosed.remove('representation_id')
var_choosed.extend(['start_date_time', 'event_id'])
merge_3 = pd.merge(representations, merge_2, left_on='id', right_on='representation_id', how='inner')[var_choosed]

var_choosed.remove('event_id')
var_choosed.extend(['name', 'customer_id'])
merge_4 = pd.merge(events, merge_3, left_on='id', right_on='event_id', how='inner')[var_choosed]

# Changement de nom
merge_4 = merge_4.rename(columns={'name': 'event_name'})
var_choosed[var_choosed.index('name')] = "event_name"

# Base finale
var_choosed.extend(['age', 'gender', 'country', 'fidelity', 'profession'])
df_customer_event = pd.merge(customersplus, merge_4, left_on = 'id', right_on = 'customer_id', how = 'inner')[var_choosed]
df_customer_event

id_x              purchase_date  type_of  is_from_subscription  \
0        992423  2023-01-11 17:08:41+01:00        3                 False   
1        992423  2023-01-11 17:08:41+01:00        3                 False   
2       1053934  2023-03-16 16:23:10+01:00        3                 False   
3       1053934  2023-03-16 16:23:10+01:00        3                 False   
4       1189141  2020-11-26 13:12:53+01:00        3                 False   
...         ...                        ...      ...                   ...   
318964  1090839  2019-05-19 21:18:36+02:00        1                 False   
318965  1090839  2019-05-19 21:18:36+02:00        1                 False   
318966  1090839  2019-05-19 21:18:36+02:00        1                 False   
318967  1244277  2019-12-31 11:04:07+01:00        1                 False   
318968  1244277  2019-12-31 11:04:07+01:00        1                 False   

        amount  is_full_price            start_date_time            event_name  
0         13.0          False  2023-02-06 20:00:00+01:00                 zaide  
1         13.0          False  2023-02-06 20:00:00+01:00                 zaide  
2         62.0          False  2023-03-19 16:00:00+01:00          luisa miller  
3         62.0          False  2023-03-19 16:00:00+01:00          luisa miller  
4         51.3          False  2020-12-01 20:00:00+01:00  iphigenie en tauride  
...        ...            ...                        ...                   ...  
318964     4.5          False  2019-05-27 20:00:00+02:00          entre femmes  
318965     4.5          False  2019-05-27 20:00:00+02:00          entre femmes  
318966     4.5          False  2019-05-27 20:00:00+02:00          entre femmes  
318967     5.5          False  2020-02-03 20:00:00+01:00   a boire et a manger  
318968     5.5          False  2020-02-03 20:00:00+01:00   a boire et a manger  

[318969 rows x 8 columns]

## Type de client au globale

In [4]:
# Client
print(customer_target_mappings.columns)
print(customer_target_mappings.shape)
customer_target_mappings.info()

Index(['id', 'customer_id', 'target_id', 'created_at', 'updated_at', 'name',
       'extra_field'],
      dtype='object')
(124302, 7)
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 124302 entries, 0 to 124301
Data columns (total 7 columns):
 #   Column       Non-Null Count   Dtype  
---  ------       --------------   -----  
 0   id           124302 non-null  int64  
 1   customer_id  124302 non-null  int64  
 2   target_id    124302 non-null  int64  
 3   created_at   124296 non-null  object 
 4   updated_at   124296 non-null  object 
 5   name         0 non-null       float64
 6   extra_field  0 non-null       float64
dtypes: float64(2), int64(3), object(2)
memory usage: 6.6+ MB


In [26]:
customer_target_mappings['extra_field'].unique()

array([nan])

In [27]:
customer_target_mappings['name'].unique()

array([nan])

In [11]:
# Segmentation existante
print(target_types.columns)
print(target_types.shape)
target_types.info()

Index(['id', 'is_import', 'name', 'created_at', 'updated_at', 'identifier'], dtype='object')
(4, 6)
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4 entries, 0 to 3
Data columns (total 6 columns):
 #   Column      Non-Null Count  Dtype 
---  ------      --------------  ----- 
 0   id          4 non-null      int64 
 1   is_import   4 non-null      bool  
 2   name        4 non-null      object
 3   created_at  4 non-null      object
 4   updated_at  4 non-null      object
 5   identifier  4 non-null      object
dtypes: bool(1), int64(1), object(4)
memory usage: 292.0+ bytes


In [12]:
target_types

id  is_import                   name                        created_at  \
0   1      False   manual_static_filter  2021-04-29 13:42:14.111085+02:00   
1   3       True       manual_structure  2021-05-07 15:20:00.626650+02:00   
2   6      False  manual_dynamic_filter  2021-09-09 14:27:47.641302+02:00   
3   2       True          manual_import  2021-04-29 13:49:30.107110+02:00   

                         updated_at                        identifier  
0  2021-04-29 13:42:14.111085+02:00  fb27e81baa4debc6a4e1a8639c20e808  
1  2021-05-07 15:20:00.626650+02:00  382bca214204a2d3462f5ec2728d5d1e  
2  2021-09-09 14:27:47.641302+02:00  e0f4b8693184850fefd6d2a38f10584e  
3  2021-04-29 13:49:30.107110+02:00  12213df2ce68a624e4c0070521437bac

In [17]:
# Tags = clients
FILE_PATH_S3 = 'bdc2324-data/11/11tags.csv'

with fs.open(FILE_PATH_S3, mode="rb") as file_in:
    tags = pd.read_csv(file_in, sep=",")

print(tags.columns)
print(tags.shape)
tags.info()

Index(['id', 'name', 'created_at', 'updated_at', 'identifier'], dtype='object')
(20, 5)
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 20 entries, 0 to 19
Data columns (total 5 columns):
 #   Column      Non-Null Count  Dtype 
---  ------      --------------  ----- 
 0   id          20 non-null     int64 
 1   name        19 non-null     object
 2   created_at  20 non-null     object
 3   updated_at  20 non-null     object
 4   identifier  20 non-null     object
dtypes: int64(1), object(4)
memory usage: 928.0+ bytes


In [18]:
tags

id                                     name  \
0    2                               ens-écoles   
1    1                                      NaN   
2    4                  ecoles primaires rennes   
3    5                      Angers Nantes Opéra   
4    6                                   Opéras   
5    7                  Ministère de la Culture   
6    8                               Orchestres   
7    9                              Cooperative   
8   10                                 Théâtres   
9   11                         La co[opera]tive   
10  12                          Ville de Rennes   
11  13                   Ensembles en résidence   
12  14                                Ministère   
13  15                         Rennes métropole   
14  16  Ville de Rennes - équipements culturels   
15  17         Structures culturelles rennaises   
16  18                      Université Rennes 2   
17  19        Centres chorégraphiques nationaux   
18  20                               Télévision   
19  21        structures culturelles nationales   

                          created_at                        updated_at  \
0   2021-05-07 15:24:19.808501+02:00  2021-05-07 15:24:19.808501+02:00   
1   2021-05-07 15:24:19.805589+02:00  2021-05-07 15:24:19.805589+02:00   
2   2021-05-07 15:29:06.388415+02:00  2021-05-07 15:29:06.388415+02:00   
3   2023-01-27 15:59:58.187557+01:00  2023-01-27 15:59:58.187557+01:00   
4   2023-01-27 16:03:59.654938+01:00  2023-01-27 16:03:59.654938+01:00   
5   2023-01-30 11:22:29.636813+01:00  2023-01-30 11:22:29.636813+01:00   
6   2023-01-30 11:33:56.392799+01:00  2023-01-30 11:33:56.392799+01:00   
7   2023-01-31 14:44:38.471146+01:00  2023-01-31 14:44:38.471146+01:00   
8   2023-01-31 14:45:17.804428+01:00  2023-01-31 14:45:17.804428+01:00   
9   2023-02-16 17:11:35.004478+01:00  2023-02-16 17:11:35.004478+01:00   
10  2023-02-16 17:37:13.816196+01:00  2023-02-16 17:37:13.816196+01:00   
11  2023-02-16 17:55:54.877374+01:00  2023-02-16 17:55:54.877374+01:00   
12  2023-02-17 11:17:54.429462+01:00  2023-02-17 11:17:54.429462+01:00   
13  2023-02-17 11:53:24.490786+01:00  2023-02-17 11:53:24.490786+01:00   
14  2023-02-17 12:00:10.649104+01:00  2023-02-17 12:00:10.649104+01:00   
15  2023-02-17 12:05:55.583016+01:00  2023-02-17 12:05:55.583016+01:00   
16  2023-02-17 14:23:44.832959+01:00  2023-02-17 14:23:44.832959+01:00   
17  2023-02-17 15:29:41.827321+01:00  2023-02-17 15:29:41.827321+01:00   
18  2023-02-17 15:46:13.746092+01:00  2023-02-17 15:46:13.746092+01:00   
19  2023-02-17 15:56:00.555722+01:00  2023-02-17 15:56:00.555722+01:00   

                          identifier  
0   b6a360c5f84595940c5774f13fd39cc3  
1   d41d8cd98f00b204e9800998ecf8427e  
2   ca8649dd64c240d118f60b07d11a7053  
3   f8f500f937fe312542399299cdc13f7e  
4   22eb2c616983ec7b54a093f84b230505  
5   1b8c5c08fde000d90905a3d14af7763d  
6   7c2aee0c80642d7e325a450f2dec45e5  
7   6c88c36ffaab88d255865aa3111d7686  
8   b2c19672df82021702b79482c8cda85a  
9   5dbaa3a1f278c0fcf981d447ad20957a  
10  bc483d04d9c3a08f167a3ce64366ca72  
11  e70635e771de13268dccf02bb2abfaf9  
12  a3f0582853fd19f5b57e3651f8a20e7a  
13  e98b8db5941b96c29c353b6f2f502055  
14  a44edffc7edb852982efa7f4aa6d0e25  
15  241550517e4e3b1c926e9aeab0f621cd  
16  4057c5cee51c4e10aa819f0cf48adc3f  
17  41e75941dfb766365498d917abe0102f  
18  36d6409c539dd79c1f3af8c5948603eb  
19  5311cf7e42aac53289e1c4a338d5cfa4

In [19]:
# Structure = clients
FILE_PATH_S3 = 'bdc2324-data/11/11structure_tag_mappings.csv'

with fs.open(FILE_PATH_S3, mode="rb") as file_in:
    structure_tag_mappings = pd.read_csv(file_in, sep=",")

print(structure_tag_mappings.columns)
print(structure_tag_mappings.shape)
structure_tag_mappings.info()

Index(['id', 'structure_id', 'tag_id', 'created_at', 'updated_at'], dtype='object')
(179, 5)
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 179 entries, 0 to 178
Data columns (total 5 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   id            179 non-null    int64 
 1   structure_id  179 non-null    int64 
 2   tag_id        179 non-null    int64 
 3   created_at    179 non-null    object
 4   updated_at    179 non-null    object
dtypes: int64(3), object(2)
memory usage: 7.1+ KB


In [20]:
structure_tag_mappings

id  structure_id  tag_id                        created_at  \
0    123           187       6  2023-01-27 16:03:59.680222+01:00   
1      2             2       2  2021-05-07 15:24:19.872895+02:00   
2      3             3       2  2021-05-07 15:24:19.873830+02:00   
3      4             4       2  2021-05-07 15:24:19.874628+02:00   
4      5             5       2  2021-05-07 15:24:19.875421+02:00   
..   ...           ...     ...                               ...   
174  184           236      10  2023-02-17 16:35:25.041114+01:00   
175  185           237      17  2023-02-17 16:39:10.799478+01:00   
176  186           238      19  2023-02-17 16:53:21.098690+01:00   
177  187           239      10  2023-02-17 16:57:42.623481+01:00   
178  188           240      10  2023-02-17 16:59:22.067723+01:00   

                           updated_at  
0    2023-01-27 16:03:59.680222+01:00  
1    2021-05-07 15:24:19.872895+02:00  
2    2021-05-07 15:24:19.873830+02:00  
3    2021-05-07 15:24:19.874628+02:00  
4    2021-05-07 15:24:19.875421+02:00  
..                                ...  
174  2023-02-17 16:35:25.041114+01:00  
175  2023-02-17 16:39:10.799478+01:00  
176  2023-02-17 16:53:21.098690+01:00  
177  2023-02-17 16:57:42.623481+01:00  
178  2023-02-17 16:59:22.067723+01:00  

[179 rows x 5 columns]

In [24]:
# Tags = clients
FILE_PATH_S3 = 'bdc2324-data/11/11customersplus.csv'

with fs.open(FILE_PATH_S3, mode="rb") as file_in:
    customersplus = pd.read_csv(file_in, sep=",")

print(customersplus.columns)
print(customersplus.shape)
customersplus.info()

Index(['id', 'lastname', 'firstname', 'birthdate', 'email', 'street_id',
       'created_at', 'updated_at', 'civility', 'is_partner', 'extra',
       'deleted_at', 'reference', 'gender', 'is_email_true', 'extra_field',
       'identifier', 'opt_in', 'structure_id', 'note', 'profession',
       'language', 'mcp_contact_id', 'need_reload', 'last_buying_date',
       'max_price', 'ticket_sum', 'average_price', 'fidelity',
       'average_purchase_delay', 'average_price_basket',
       'average_ticket_basket', 'total_price', 'preferred_category',
       'preferred_supplier', 'preferred_formula', 'purchase_count',
       'first_buying_date', 'last_visiting_date', 'zipcode', 'country', 'age',
       'tenant_id'],
      dtype='object')
(71307, 43)
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 71307 entries, 0 to 71306
Data columns (total 43 columns):
 #   Column                  Non-Null Count  Dtype  
---  ------                  --------------  -----  
 0   id                      71307

In [25]:
customersplus

id        lastname        firstname   birthdate        email  \
0      286834  lastname286834  firstname286834         NaN  email286834   
1      330695             NaN              NaN         NaN  email330695   
2      330978             NaN              NaN         NaN  email330978   
3      338697             NaN              NaN         NaN  email338697   
4      338726             NaN              NaN         NaN  email338726   
...       ...             ...              ...         ...          ...   
71302   27105   lastname27105   firstname27105  1957-01-26   email27105   
71303   27108   lastname27108   firstname27108         NaN          NaN   
71304   27110   lastname27110   firstname27110         NaN          NaN   
71305   10607   lastname10607   firstname10607  1963-01-04   email10607   
71306   19095   lastname19095   firstname19095  1979-07-16   email19095   

       street_id                        created_at  \
0              6  2022-05-19 10:09:09.361137+02:00   
1              1  2022-07-16 04:10:34.135134+02:00   
2              1  2022-07-21 22:14:09.811721+02:00   
3              1  2022-09-15 19:02:03.950536+02:00   
4              1  2022-09-16 01:24:40.719882+02:00   
...          ...                               ...   
71302     205024  2021-04-22 15:12:59.986534+02:00   
71303     205024  2021-04-22 15:12:59.989197+02:00   
71304          6  2021-04-22 15:12:59.991029+02:00   
71305     313332  2021-04-22 14:56:45.742226+02:00   
71306          6  2021-04-22 15:06:30.120537+02:00   

                             updated_at  civility  is_partner  ...  \
0      2022-05-19 10:09:09.361137+02:00       NaN       False  ...   
1      2022-07-16 04:10:34.156704+02:00       NaN       False  ...   
2      2022-07-21 22:14:09.836051+02:00       NaN       False  ...   
3      2022-09-15 19:02:03.985642+02:00       NaN       False  ...   
4      2022-09-16 01:24:40.742753+02:00       NaN       False  ...   
...                                 ...       ...         ...  ...   
71302  2023-09-12 18:59:31.613235+02:00       NaN       False  ...   
71303  2023-09-12 18:27:34.380843+02:00       NaN       False  ...   
71304  2022-04-14 11:41:33.738500+02:00       NaN       False  ...   
71305  2023-09-12 17:55:17.723195+02:00       NaN       False  ...   
71306  2023-09-12 18:27:36.904104+02:00       NaN       False  ...   

       preferred_category  preferred_supplier  preferred_formula  \
0                     NaN                 NaN                NaN   
1                     NaN                 NaN                NaN   
2                     NaN                 NaN                NaN   
3                     NaN                 NaN                NaN   
4                     NaN                 NaN                NaN   
...                   ...                 ...                ...   
71302                 NaN                 NaN                NaN   
71303                 NaN                 NaN                NaN   
71304                 NaN                 NaN                NaN   
71305                 NaN                 NaN                NaN   
71306                 NaN                 NaN                NaN   

       purchase_count          first_buying_date  last_visiting_date zipcode  \
0                   0                        NaN                 NaN     NaN   
1                   0                        NaN                 NaN     NaN   
2                   0                        NaN                 NaN     NaN   
3                   0                        NaN                 NaN     NaN   
4                   0                        NaN                 NaN     NaN   
...               ...                        ...                 ...     ...   
71302               2  2018-12-31 18:56:57+01:00                 NaN   35700   
71303               6  2015-12-29 14:51:46+01:00                 NaN   35700   
71304               1  2018-12-31 19:12:59+01:00                 NaN     NaN   
713

In [6]:
# But : lier les caractéristiques socio-demo et les comportements d'achat


In [29]:
# tickets
FILE_PATH_S3 = 'bdc2324-data/11/11tickets.csv'

with fs.open(FILE_PATH_S3, mode="rb") as file_in:
    tickets = pd.read_csv(file_in, sep=",")

print(tickets.columns)
print(tickets.shape)
tickets.info()

Index(['id', 'number', 'created_at', 'updated_at', 'purchase_id', 'product_id',
       'is_from_subscription', 'type_of', 'supplier_id', 'barcode',
       'identifier'],
      dtype='object')
(318969, 11)
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 318969 entries, 0 to 318968
Data columns (total 11 columns):
 #   Column                Non-Null Count   Dtype  
---  ------                --------------   -----  
 0   id                    318969 non-null  int64  
 1   number                318969 non-null  object 
 2   created_at            318969 non-null  object 
 3   updated_at            318969 non-null  object 
 4   purchase_id           318969 non-null  int64  
 5   product_id            318969 non-null  int64  
 6   is_from_subscription  318969 non-null  bool   
 7   type_of               318969 non-null  int64  
 8   supplier_id           318969 non-null  int64  
 9   barcode               0 non-null       float64
 10  identifier            318969 non-null  object 
dtypes: 

In [30]:
tickets

id               number                        created_at  \
0       2119081   1433_136_212_68356  2023-09-12 17:42:45.396336+02:00   
1       2119082   1433_136_194_68356  2023-09-12 17:42:45.409056+02:00   
2       2119083  33158_158_343_68357  2023-09-12 17:42:45.409824+02:00   
3       2119084  33158_158_297_68357  2023-09-12 17:42:45.410447+02:00   
4       2119085  33158_158_318_68357  2023-09-12 17:42:45.411059+02:00   
...         ...                  ...                               ...   
318964  2564021  44247_204_239_89278  2023-09-12 18:59:48.750953+02:00   
318965  2564022  44247_204_299_89278  2023-09-12 18:59:48.751441+02:00   
318966  2564023  44247_204_259_89278  2023-09-12 18:59:48.751924+02:00   
318967  2564024  44247_204_279_89278  2023-09-12 18:59:48.752425+02:00   
318968  2513156  4854_178_2847_89170  2023-09-12 18:52:20.331807+02:00   

                              updated_at  purchase_id  product_id  \
0       2023-09-12 17:42:45.396336+02:00       861764      209879   
1       2023-09-12 17:42:45.409056+02:00       861763      209879   
2       2023-09-12 17:42:45.409824+02:00       861769      209880   
3       2023-09-12 17:42:45.410447+02:00       861767      209880   
4       2023-09-12 17:42:45.411059+02:00       861768      209880   
...                                  ...          ...         ...   
318964  2023-09-12 18:59:48.750953+02:00      1244281      210158   
318965  2023-09-12 18:59:48.751441+02:00      1244284      210158   
318966  2023-09-12 18:59:48.751924+02:00      1244282      210158   
318967  2023-09-12 18:59:48.752425+02:00      1244283      210158   
318968  2023-09-12 18:59:48.752904+02:00      1244285      261922   

        is_from_subscription  type_of  supplier_id  barcode  \
0                      False        1         1702      NaN   
1                      False        1         1702      NaN   
2                      False        1         1702      NaN   
3                      False        1         1702      NaN   
4                      False        1         1702      NaN   
...                      ...      ...          ...      ...   
318964                 False        1         1702      NaN   
318965                 False        1         1702      NaN   
318966                 False        1         1702      NaN   
318967                 False        1         1702      NaN   
318968                 False        3         1702      NaN   

                              identifier  
0       f694c255855ce5643c6fcc7fed5e9237  
1       838d6101db2fc8bc80536d8b91b49859  
2       8a8d938d66a4dc57bcb44c2773c6fdfa  
3       b7a3dd0794c0957c942d45b8913e5b96  
4       d7ea7e443581ebe520dd13f6cad31af7  
...                                  ...  
318964  82c9af8b2167f7ac34a5e834242b0239  
318965  235e8e608f066cb72949bbd397d0a76f  
318966  ec22fa828931f030f7e79a4cc5478c4b  
318967  31ec4deaf718e04caf193e1ff8d621ef  
318968  48aef9efab29bfb1537656908863bcc1  

[318969 rows x 11 columns]

In [33]:
tickets['type_of'].unique()

array([1, 3, 0])

## Types d'évenement et client

In [6]:
# Evenement = events.csv
FILE_PATH_S3 = 'bdc2324-data/11/11events.csv'

with fs.open(FILE_PATH_S3, mode="rb") as file_in:
    events = pd.read_csv(file_in, sep=",")

print(events.columns)
print(events.shape)
events.info()

Index(['id', 'created_at', 'updated_at', 'season_id', 'facility_id', 'name',
       'event_type_id', 'manual_added', 'is_display', 'event_type_key_id',
       'facility_key_id', 'identifier'],
      dtype='object')
(403, 12)
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 403 entries, 0 to 402
Data columns (total 12 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   id                 403 non-null    int64 
 1   created_at         403 non-null    object
 2   updated_at         403 non-null    object
 3   season_id          403 non-null    int64 
 4   facility_id        403 non-null    int64 
 5   name               403 non-null    object
 6   event_type_id      403 non-null    int64 
 7   manual_added       403 non-null    bool  
 8   is_display         403 non-null    bool  
 9   event_type_key_id  403 non-null    int64 
 10  facility_key_id    403 non-null    int64 
 11  identifier         403 non-null    object
dtypes: bool

In [7]:
events

id                        created_at  \
0    20367  2023-09-13 03:42:45.214293+02:00   
1    20371  2023-09-13 03:42:45.218728+02:00   
2    20570  2023-10-05 04:48:29.374504+02:00   
3    20757  2023-11-01 03:55:20.846196+01:00   
4    20364  2023-09-13 03:42:45.196791+02:00   
..     ...                               ...   
398  15603  2023-09-12 17:42:25.327618+02:00   
399  15621  2023-09-12 17:42:25.335792+02:00   
400  15740  2023-09-12 17:47:05.112101+02:00   
401  15520  2023-09-12 17:42:25.290280+02:00   
402  15439  2023-09-12 17:42:25.252747+02:00   

                           updated_at  season_id  facility_id  \
0    2023-09-13 03:54:30.086969+02:00       1865         1054   
1    2023-09-13 03:54:30.103943+02:00       1865         1054   
2    2023-10-05 04:48:36.562528+02:00       1865         1054   
3    2023-11-01 03:55:28.412457+01:00       1865         1054   
4    2023-09-13 03:54:30.075456+02:00       1865         1054   
..                                ...        ...          ...   
398  2023-09-12 19:00:00.893400+02:00       1706         1054   
399  2023-09-12 19:00:00.899622+02:00       1708         1054   
400  2023-09-12 19:00:00.906123+02:00       1711         1054   
401  2023-09-12 19:00:00.835625+02:00       1708         1054   
402  2023-09-12 19:00:00.735990+02:00       1708         1054   

                                 name  event_type_id  manual_added  \
0                             marelle           1055         False   
1                           dialogues           1055         False   
2                 les grandes epopees           1055         False   
3                    scolaire marelle           1055         False   
4           le couronnement de poppee           1055         False   
..                                ...            ...           ...   
398                           marelle           1055         False   
399                 cartes d'adhesion           1055         False   
400  repetition le medecin malgre lui           1055         False   
401                  opera au village           1055         False   
402                         florilege           1055         False   

     is_display  event_type_key_id  facility_key_id  \
0          True               1055             1054   
1          True               1055             1054   
2          True               1055             1054   
3          True               1055             1054   
4          True               1055             1054   
..          ...                ...              ...   
398        True               1055             1054   
399        True               1055             1054   
400        True               1055             1054   
401        True               1055             1054   
402        True               1055             1054   

                           identifier  
0    26d1e9a4acad18b9cf79244334c86c93  
1    60356fc5e8ed6c9c1be9c5ec67e77766  
2    f8ab088e06252bf34e1b12ad2ce1a403  
3    447fa80f9a793b7587bb85ebbda6442c  
4    3b37f5d2cd354cbc422868621ac7ebc2  
..                                ...  
398  fde88b72fb82b1fe42fbbfbfc3d6b4d3  
399  051b96aad2b720bad4450a59ed7dfbf6  
400  addd6885bea5ddf60ec3539dfc3e79e8  
401  94f250d10d4a56358ceab23b384439ff  
402  4f015946bcbd856aa573cadb7ac42b9f  

[403 rows x 12 columns]

In [15]:
events['name'].nunique()

357

In [16]:
# Représentation des évenements = representations.csv
FILE_PATH_S3 = 'bdc2324-data/11/11representations.csv'

with fs.open(FILE_PATH_S3, mode="rb") as file_in:
    representations = pd.read_csv(file_in, sep=",")

print(representations.columns)
print(representations.shape)
representations.info()

Index(['id', 'serial', 'event_id', 'created_at', 'updated_at',
       'start_date_time', 'open', 'satisfaction', 'end_date_time', 'name',
       'is_display', 'representation_type_id', 'expected_filling',
       'max_filling', 'extra_field', 'identifier'],
      dtype='object')
(996, 16)
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 996 entries, 0 to 995
Data columns (total 16 columns):
 #   Column                  Non-Null Count  Dtype  
---  ------                  --------------  -----  
 0   id                      996 non-null    int64  
 1   serial                  0 non-null      float64
 2   event_id                996 non-null    int64  
 3   created_at              996 non-null    object 
 4   updated_at              996 non-null    object 
 5   start_date_time         996 non-null    object 
 6   open                    996 non-null    bool   
 7   satisfaction            0 non-null      float64
 8   end_date_time           996 non-null    object 
 9   name              

In [17]:
representations

id  serial  event_id                        created_at  \
0    44351     NaN     20371  2023-09-13 03:42:45.245879+02:00   
1    45497     NaN     20757  2023-11-01 03:55:20.875712+01:00   
2    44383     NaN     20383  2023-09-13 10:41:08.964302+02:00   
3    44384     NaN     20383  2023-09-13 10:41:08.972401+02:00   
4    44385     NaN     20384  2023-09-13 10:41:08.973290+02:00   
..     ...     ...       ...                               ...   
991  33894     NaN     15647  2023-09-12 17:42:25.564297+02:00   
992  33873     NaN     15640  2023-09-12 17:42:25.554863+02:00   
993  33610     NaN     15520  2023-09-12 17:42:25.442979+02:00   
994  33953     NaN     15520  2023-09-12 17:42:25.590746+02:00   
995  33639     NaN     15533  2023-09-12 17:42:25.455708+02:00   

                           updated_at            start_date_time  open  \
0    2023-09-13 03:42:45.245879+02:00  2023-12-21 20:00:00+01:00  True   
1    2023-11-01 03:55:20.875712+01:00  2023-11-28 10:00:00+01:00  True   
2    2023-09-13 10:41:08.964302+02:00  2023-06-04 17:00:00+02:00  True   
3    2023-09-13 10:41:08.972401+02:00  2023-06-03 17:30:00+02:00  True   
4    2023-09-13 10:41:08.973290+02:00  2023-06-03 16:15:00+02:00  True   
..                                ...                        ...   ...   
991  2023-09-12 17:42:25.564297+02:00  2022-11-08 20:00:00+01:00  True   
992  2023-09-12 17:42:25.554863+02:00  2022-11-14 20:00:00+01:00  True   
993  2023-09-12 17:42:25.442979+02:00  2023-06-19 18:00:00+02:00  True   
994  2023-09-12 17:42:25.590746+02:00  2023-06-19 20:00:00+02:00  True   
995  2023-09-12 17:42:25.455708+02:00  2023-04-15 17:30:00+02:00  True   

     satisfaction              end_date_time  name  is_display  \
0             NaN  1901-01-01 00:09:21+00:09   NaN        True   
1             NaN  1901-01-01 00:09:21+00:09   NaN        True   
2             NaN  1901-01-01 00:09:21+00:09   NaN        True   
3             NaN  1901-01-01 00:09:21+00:09   NaN        True   
4             NaN  1901-01-01 00:09:21+00:09   NaN        True   
..            ...                        ...   ...         ...   
991           NaN  1901-01-01 00:09:21+00:09   NaN        True   
992           NaN  1901-01-01 00:09:21+00:09   NaN        True   
993           NaN  1901-01-01 00:09:21+00:09   NaN        True   
994           NaN  1901-01-01 00:09:21+00:09   NaN        True   
995           NaN  1901-01-01 00:09:21+00:09   NaN        True   

     representation_type_id  expected_filling  max_filling  extra_field  \
0                       NaN             550.0        550.0          NaN   
1                       NaN               NaN          NaN          NaN   
2                       NaN               NaN          NaN          NaN   
3                       NaN               NaN          NaN          NaN   
4                       NaN               NaN          NaN          NaN   
..                      ...               ...          ...          ...   
991                     NaN               NaN          NaN          NaN   
992                     NaN               NaN          NaN          NaN   
993                     NaN               NaN          NaN          NaN   
994                     NaN               NaN          NaN          NaN   
995                     NaN               NaN          NaN          NaN   

                           identifier  
0    33520762e8cc28982e3841cbc2be8ce2  
1    5c34b84e3d11276e0995d984c94cd28d  
2    bf3c65a1dfefbd747dcc2360e6887eac  
3    b0e69ae8b78ebab3066aac83de22d239  
4    9fb91c8b1cf9e444111c511e212ac5c1  
..                                ...  
991  44bbcecfd007ceaad05805391beccabb  
992  151edbec8e0a3cd80071038e857f3493  
993  9e9e38d527427e1b6f67e0c3f12b82fc  
994  7bf0978aabb6cac1bb4cd2784afb2b6b  
995  fae68f1e09710ec8747957af6e22f61d  

[996 rows x 16 columns]

In [18]:
# Produits vendues = products.csv
FILE_PATH_S3 = 'bdc2324-data/11/11products.csv'

with fs.open(FILE_PATH_S3, mode="rb") as file_in:
    products = pd.read_csv(file_in, sep=",")

print(products.columns)
print(products.shape)
products.info()

Index(['id', 'amount', 'is_full_price', 'representation_id',
       'pricing_formula_id', 'created_at', 'updated_at', 'category_id',
       'apply_price', 'products_group_id', 'product_pack_id', 'extra_field',
       'amount_consumption', 'identifier'],
      dtype='object')
(14648, 14)
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 14648 entries, 0 to 14647
Data columns (total 14 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   id                  14648 non-null  int64  
 1   amount              14648 non-null  float64
 2   is_full_price       14648 non-null  bool   
 3   representation_id   14648 non-null  int64  
 4   pricing_formula_id  14648 non-null  int64  
 5   created_at          14648 non-null  object 
 6   updated_at          14648 non-null  object 
 7   category_id         14648 non-null  int64  
 8   apply_price         14648 non-null  float64
 9   products_group_id   14648 non-null  int64  
 10  product_pa

In [19]:
products

id  amount  is_full_price  representation_id  pricing_formula_id  \
0      268325    18.0          False              44332               20477   
1      274118    36.8          False              44340               20502   
2      268338    39.1          False              44340               20497   
3      209883     0.0          False              33443               20475   
4      268326    63.0          False              44333               20477   
...       ...     ...            ...                ...                 ...   
14643  217878    33.6          False              33919               20489   
14644  268315    10.0          False              33919               20504   
14645  210148     5.0          False              33531               20473   
14646  212054    30.0          False              33810               20473   
14647  261922    21.0          False              33766               20488   

                             created_at                        updated_at  \
0      2023-09-13 03:42:45.415594+02:00  2023-09-13 03:42:45.415594+02:00   
1      2023-10-25 03:26:57.430694+02:00  2023-10-25 03:26:57.430694+02:00   
2      2023-09-13 03:42:45.430942+02:00  2023-09-13 03:42:45.430942+02:00   
3      2023-09-12 17:42:27.595998+02:00  2023-09-12 17:42:27.595998+02:00   
4      2023-09-13 03:42:45.417283+02:00  2023-09-13 03:42:45.417283+02:00   
...                                 ...                               ...   
14643  2023-09-12 17:51:11.572882+02:00  2023-09-12 17:51:11.572882+02:00   
14644  2023-09-12 18:59:29.995176+02:00  2023-09-12 18:59:29.995176+02:00   
14645  2023-09-12 17:42:27.733260+02:00  2023-09-12 17:42:27.733260+02:00   
14646  2023-09-12 17:42:28.724681+02:00  2023-09-12 17:42:28.724681+02:00   
14647  2023-09-12 18:52:00.519838+02:00  2023-09-12 18:52:00.519838+02:00   

       category_id  apply_price  products_group_id  product_pack_id  \
0             4972          0.0             268108                1   
1             4969          0.0             273901                1   
2             4969          0.0             268121                1   
3             4970          0.0             209706                1   
4             4969          0.0             268109                1   
...            ...          ...                ...              ...   
14643         4971          0.0             217695                1   
14644         4969          0.0             268098                1   
14645         4975          0.0             209971                1   
14646         4972          0.0             211876                1   
14647         4972          0.0             261709                1   

       extra_field  amount_consumption                        identifier  
0              NaN                 NaN  b823bbea3ba837da2ef8efaf1287272d  
1              NaN                 NaN  81e8b7991f6948e3ef7cfe5011d13532  
2              NaN                 NaN  be8bc0399db4d04aefa9f44afd4d5efa  
3              NaN                 NaN  01a9eea5f8ad53491faa864bfac44183  
4              NaN                 NaN  781a917ecfdabb14169701d7b143bbe4  
...            ...                 ...                               ...  
14643          NaN                 NaN  82bba69321466069411b3023343b44a4  
14644          NaN                 NaN  eae56a8eb0a4315c5713b2053103d595  
14645          NaN                 NaN  449f86c1ef2b478d3389f7d0e27d0e6b  
14646          NaN                 NaN  2090203e2c0b58ea8f505089faee6d62  
14647          NaN                 NaN  9139ee36a92bed766ae95372cca77336  

[14648 rows x 14 columns]

In [20]:
# Lieu = facilities.csv
FILE_PATH_S3 = 'bdc2324-data/11/11facilities.csv'

with fs.open(FILE_PATH_S3, mode="rb") as file_in:
    facilities = pd.read_csv(file_in, sep=",")

print(facilities.columns)
print(facilities.shape)
facilities.info()

Index(['id', 'name', 'created_at', 'updated_at', 'street_id', 'fixed_capacity',
       'identifier'],
      dtype='object')
(1, 7)
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1 entries, 0 to 0
Data columns (total 7 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   id              1 non-null      int64  
 1   name            0 non-null      float64
 2   created_at      1 non-null      object 
 3   updated_at      1 non-null      object 
 4   street_id       1 non-null      int64  
 5   fixed_capacity  0 non-null      float64
 6   identifier      1 non-null      object 
dtypes: float64(2), int64(2), object(3)
memory usage: 184.0+ bytes


In [21]:
facilities

id  name                        created_at  \
0  1054   NaN  2023-09-12 17:42:25.223064+02:00   

                         updated_at  street_id  fixed_capacity  \
0  2023-09-12 17:42:25.223064+02:00          1             NaN   

                         identifier  
0  d41d8cd98f00b204e9800998ecf8427e

In [22]:
# Saisons = seasons.csv période sur deux années consécutives
FILE_PATH_S3 = 'bdc2324-data/11/11seasons.csv'

with fs.open(FILE_PATH_S3, mode="rb") as file_in:
    seasons = pd.read_csv(file_in, sep=",")

print(seasons.columns)
print(seasons.shape)
seasons.info()

Index(['id', 'name', 'created_at', 'updated_at', 'start_date_time',
       'identifier'],
      dtype='object')
(9, 6)
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 9 entries, 0 to 8
Data columns (total 6 columns):
 #   Column           Non-Null Count  Dtype  
---  ------           --------------  -----  
 0   id               9 non-null      int64  
 1   name             9 non-null      object 
 2   created_at       9 non-null      object 
 3   updated_at       9 non-null      object 
 4   start_date_time  0 non-null      float64
 5   identifier       9 non-null      object 
dtypes: float64(1), int64(1), object(4)
memory usage: 560.0+ bytes


In [24]:
seasons['name'].unique()

array(['saison 2023-2024', 'saison 2021-2022', 'saison 2015-2016',
       'saison 2016-2017', 'saison 2017-2018', 'saison 2018-2019',
       'saison 2020-2021', 'saison 2019-2020', 'saison 2022-2023'],
      dtype=object)

In [25]:
# Achats = purchases.csv 
FILE_PATH_S3 = 'bdc2324-data/11/11purchases.csv'

with fs.open(FILE_PATH_S3, mode="rb") as file_in:
    purchases = pd.read_csv(file_in, sep=",")

print(purchases.columns)
print(purchases.shape)
purchases.info()

Index(['id', 'purchase_date', 'customer_id', 'created_at', 'updated_at',
       'number', 'identifier'],
      dtype='object')
(410695, 7)
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 410695 entries, 0 to 410694
Data columns (total 7 columns):
 #   Column         Non-Null Count   Dtype  
---  ------         --------------   -----  
 0   id             410695 non-null  int64  
 1   purchase_date  410695 non-null  object 
 2   customer_id    410695 non-null  int64  
 3   created_at     410695 non-null  object 
 4   updated_at     410695 non-null  object 
 5   number         0 non-null       float64
 6   identifier     410695 non-null  object 
dtypes: float64(1), int64(2), object(4)
memory usage: 21.9+ MB


In [28]:
purchases

id              purchase_date  customer_id  \
0        861761  2019-03-01 16:28:49+01:00         4966   
1        861762  2019-03-01 16:29:11+01:00         4966   
2        861763  2019-03-01 16:29:17+01:00         4966   
3        861764  2019-03-01 16:29:19+01:00         4966   
4        861765  2019-03-01 16:32:08+01:00       405994   
...         ...                        ...          ...   
410690  1285964  2023-10-21 21:46:41+02:00       517309   
410691  1285965  2023-10-21 21:47:07+02:00       517309   
410692  1285966  2023-10-21 21:47:20+02:00       517309   
410693  1285967  2023-10-21 23:07:06+02:00       399969   
410694  1285968  2023-10-21 23:07:39+02:00       399969   

                              created_at                        updated_at  \
0       2023-09-12 17:42:37.564150+02:00  2023-09-12 17:42:37.564150+02:00   
1       2023-09-12 17:42:37.571159+02:00  2023-09-12 17:42:37.571159+02:00   
2       2023-09-12 17:42:37.571646+02:00  2023-09-12 17:42:37.571646+02:00   
3       2023-09-12 17:42:37.572063+02:00  2023-09-12 17:42:37.572063+02:00   
4       2023-09-12 17:42:37.572470+02:00  2023-09-12 17:42:37.572470+02:00   
...                                  ...                               ...   
410690  2023-10-23 03:43:16.457501+02:00  2023-10-23 03:43:16.457501+02:00   
410691  2023-10-23 03:43:16.458458+02:00  2023-10-23 03:43:16.458458+02:00   
410692  2023-10-23 03:43:16.458811+02:00  2023-10-23 03:43:16.458811+02:00   
410693  2023-10-23 03:43:16.459738+02:00  2023-10-23 03:43:16.459738+02:00   
410694  2023-10-23 03:43:16.462409+02:00  2023-10-23 03:43:16.462409+02:00   

        number                        identifier  
0          NaN  d20eb0c3a7efec0bbe338dee40dc3378  
1          NaN  cff3abfc018517bce5ccfc58f5cacf40  
2          NaN  e1155cf26b34f792bdb23e49244d7264  
3          NaN  e8b95cc6a1a8b103ffa39755ce3bfc4d  
4          NaN  1b763278914f1309e357abe5033a3f0f  
...        ...                               ...  
410690     NaN  72c4e90c2b151dcffc87b19ea8a0c4f1  
410691     NaN  ee65532087132145daa6154fbae050ea  
410692     NaN  7e825dd352bc6a11ab81cb8068e325e6  
410693     NaN  fdb92627a48d6ba8fa817d60a83dbea8  
410694     NaN  e9dbaff4f7037a5b0efa11263584dfad  

[410695 rows x 7 columns]